In [19]:
import numpy as np
import pandas as pd

# read node data in coordinate (x,y) format
newnodes = pd.read_excel('original.xlsm',sheet_name='Thu', index_col='ID')
nodes = pd.read_excel('original.xlsm',sheet_name='Distances',skiprows =1,index_col='id')
nodes.drop('Zip', axis=1, inplace=True)
node_number = len(nodes.index) - 1
#print(nodes)

# node 20 is depot in original file
savings = dict()
for r in nodes.index:
    for c in nodes.columns:
        if int(c) != int(r):            
            a = max(int(r), int(c))
            b = min(int(r), int(c))
            key = '(' + str(a) + ',' + str(b) + ')'
            savings[key] = nodes[20][int(r)] + nodes[20][int(c)] - nodes[c][r]

# put savings in a pandas dataframe and sort by descending
sv = pd.DataFrame.from_dict(savings, orient = 'index')
sv.rename(columns = {0:'saving'}, inplace = True)
sv.sort_values(by = ['saving'], ascending = False, inplace = True)
#print(sv.head)
newnodes


c:\users\hrsha\appdata\local\programs\python\python39\lib\site-packages\openpyxl\worksheet\_reader.py:308: UserWarning: Unknown extension is not supported and will be removed
  warn(msg)


ORDERID  FROMZIP  TOZIP  CUBE DayOfWeek  NEWCUBE   NEWORDERID
ID                                                                    
8            219     1887   1701   137       Thu      137          219
10           229     1887   1752   180       Thu      180          229
13            21     1887   1821  1396       Thu     1396           21
17             5     1887   1867   206       Thu      206            5
19           113     1887   1886   163       Thu      163          113
21           196     1887   1890   250       Thu      250          196
25           202     1887   2108   121       Thu      121          202
26       159,184     1887   2110   272       Thu      272      159,184
27       141,185     1887   2111   281       Thu      281      141,185
29    69,118,183     1887   2115   461       Thu      461   69,118,183
30   103,189,245     1887   2116   480       Thu      480  103,189,245
31            79     1887   2120   148       Thu      148           79
34           131     1887   2134   142       Thu      142          131
36            99     1887   2138   172       Thu      172           99
37        97,210     1887   2139   604       Thu      604       97,210
38      31,46,95     1887   2142   424       Thu      424     31,46,95
40           232     1887   2188   146       Thu      146          232
43   124,190,215     1887   2215   478       Thu      478  124,190,215
46            25     1887   2451  2614       Thu     2614           25
51    75,100,142     1887   2493   582       Thu      582   75,100,142
52           259     1887   2747   131       Thu      131          259
53           154     1887   2766   345       Thu      345          154
59           195     1887   3054   319       Thu      319          195
60            56     1887   3101    94       Thu       94           56
61           199     1887   3103   197       Thu      197          199
62           136     1887   3109   257       Thu      257          136
64       194,218     1887   3755   305       Thu      305      194,218
65            86     1887   3766   193       Thu      193           86
69            84     1887   4092   175       Thu      175           84
70   151,170,222     1887   4101   398       Thu      398  151,170,222
74           102     1887   6033   168       Thu      168          102
87            36     1887   6103   102       Thu      102           36
88           127     1887   6105   127       Thu      127          127
96           166     1887   6320   474       Thu      474          166
97        93,160     1887   6340   479       Thu      479       93,160
100          134     1887   6451   225       Thu      225          134
103           61     1887   6492   103       Thu      103           61
104           63     1887   6510   112       Thu      112           63
107          119     1887   6524   138       Thu      138          119
110      214,247     1887   6814   417       Thu      417      214,247
114          137     1887   6840   195       Thu      195          137
115          197     1887   6851   348       Thu      348          197
116          256     1887   6854   152       Thu      152          256
118          227     1887   6877   125       Thu      125          227
123          147     1887   6927   173       Thu      173          147

In [20]:
# convert link string to link list to handle saving's key, i.e. str(10, 6) to (10, 6)
def get_node(link):
    link = link[1:]
    link = link[:-1]
    nodes = link.split(',')
    return [int(nodes[0]), int(nodes[1])]


# determine if a node is interior to a route
def interior(node, route):
    try:
        i = route.index(node)
        # adjacent to depot, not interior
        if i == 0 or i == (len(route) - 1):
            label = False
        else:
            label = True
    except:
        label = False
    
    return label


def merge(route0, route1, link):
    if route0.index(link[0]) != (len(route0) - 1):
        route0.reverse()
    
    if route1.index(link[1]) != 0:
        route1.reverse()
        
    return route0 + route1

# sum up to obtain the total passengers belonging to a route
def sum_cap(route):
    sum_cap = 0
    for node in route:
        sum_cap += newnodes.CUBE[node]
    return sum_cap

# sum up to obtain the total distance travelled along a route
def distance_cap(route):
    distance = 0
    oldvalue = 0
    route.append(0)   
    for newlink in route:
        if oldvalue == 0:
            distance = distance + nodes[20][newlink]
        elif newlink == route[-1]:
            distance = distance + nodes[20][oldvalue]
        else:
            distance = distance + nodes[oldvalue][newlink]
        oldvalue = newlink
    route.remove(0)
    return distance


# sum up to obtain the total distance travelled along a route
def time_cap(route):
    temptimedistance = distance_cap(route)
    temptimedistance = temptimedistance*60/40
    temptimeunload = 0
    for newlink in route:
        temptimeunload = temptimeunload + max(30, 0.03*newnodes.CUBE[newlink])
        extraordercountinlocation = str(newnodes.NEWORDERID[newlink]).count(',')
        temptimeunload = temptimeunload + (30*extraordercountinlocation)
    timecount = temptimeunload + temptimedistance
    return timecount

#say 8AM to 6PM is delivery time
#first delivery completes(unloading) at 8:30AM..for loads less than 1000ft3....till 6PM..last delivery with unloading
def deliverytime_cap(route):
    deliverytimecount = time_cap(route) - (nodes[20][route[0]]*60/40)
    return deliverytimecount



# determine 4 things:
# 1. if the link in any route in routes -> determined by if count_in > 0
# 2. if yes, which node is in the route -> returned to node_sel
# 3. if yes, which route is the node belongs to -> returned to route id: i_route
# 4. are both of the nodes in the same route? -> overlap = 1, yes; otherwise, no
def which_route(link, routes):
    # assume nodes are not in any route
    node_sel = list()
    i_route = [-1, -1]
    count_in = 0
    
    for route in routes:
        for node in link:
            try:
                route.index(node)
                i_route[count_in] = routes.index(route)
                node_sel.append(node)
                count_in += 1
            except:
                a = 1
                
    if i_route[0] == i_route[1]:
        overlap = 1
    else:
        overlap = 0
        
    return node_sel, count_in, i_route, overlap


In [22]:
# create empty routes
routes = list()

# if there is any remaining customer to be served
remaining = True

# create empty orderid
orderid = []

# determine capacity of the vehicle
cap = 3200

# determine max distance driver can drive of the vehicle
distancecap = 440

# determine max time driver can drive of the vehicle
timecap = 840
deliverytimecountcap = 600
# record steps
step = 0

# get a list of nodes, excluding the depot
node_list = list(newnodes.index)
print(node_list)

# run through each link in the saving list
for link in sv.index:
    step += 1
    if remaining:

        link = get_node(link)
        node_sel, num_in, i_route, overlap = which_route(link, routes)
        print('step ', step, ':',' link',link)

        #check if both link[0] and link[1] location values both exists in the Monday excel sheet
        
        if link[0] in newnodes.index and link[1] in newnodes.index:
            # condition a. Either, neither i nor j have already been assigned to a route, 
            # ...in which case a new route is initiated including both i and j.
            if num_in == 0:
                if sum_cap(link) <= cap and distance_cap(link) <= distancecap and time_cap(link) <= timecap and deliverytime_cap(link) < deliverytimecountcap:
                    routes.append(link)
                    node_list.remove(link[0])
                    node_list.remove(link[1])
                    print('\t','Link ', link, ' fulfills criteria a), so it is created as a new route')
                else:
                    print('\t','Though Link ', link, ' fulfills criteria a), it exceeds maximum load/distance/time, so skip this link.')
    
            # condition b. Or, exactly one of the two nodes (i or j) has already been included 
            # ...in an existing route and that point is not interior to that route 
            # ...(a point is interior to a route if it is not adjacent to the depot D in the order of traversal of nodes), 
            # ...in which case the link (i, j) is added to that same route.    
            elif num_in == 1:
                n_sel = node_sel[0]
                i_rt = i_route[0]
                position = routes[i_rt].index(n_sel)
                link_temp = link.copy()
                link_temp.remove(n_sel)
                node = link_temp[0]
   
                cond1 = (not interior(n_sel, routes[i_rt]))
                cond2 = (sum_cap(routes[i_rt] + [node]) <= cap)
                cond3 = (distance_cap(routes[i_rt] + [node]) <= distancecap)
                cond4 = (time_cap(routes[i_rt] + [node]) <= timecap)
                cond5 = (deliverytime_cap(routes[i_rt] + [node]) < deliverytimecountcap)
        
   
                if cond1:
                    if cond2 and cond3 and cond4 and cond5:
                        print('\t','Link ', link, ' fulfills criteria b), so a new node is added to route ', routes[i_rt], '.')
                        if position == 0:
                            routes[i_rt].insert(0, node)
                        else:
                            routes[i_rt].append(node)
                        node_list.remove(node)
                    else:
                        print('\t','Though Link ', link, ' fulfills criteria b), it exceeds maximum load/distance/time, so skip this link.')
                        continue
                else:
                    print('\t','For Link ', link, ', node ', n_sel, ' is interior to route ', routes[i_rt], ', so skip this link')
                    continue
  
            # condition c. Or, both i and j have already been included in two different existing routes 
            # ...and neither point is interior to its route, in which case the two routes are merged.        
            else:
                if overlap == 0:
                    cond1 = (not interior(node_sel[0], routes[i_route[0]]))
                    cond2 = (not interior(node_sel[1], routes[i_route[1]]))
                    cond3 = (sum_cap(routes[i_route[0]] + routes[i_route[1]]) <= cap)
                    cond4 = (distance_cap(routes[i_route[0]] + routes[i_route[1]]) <= distancecap)
                    cond5 = (time_cap(routes[i_route[0]] + routes[i_route[1]]) <= timecap)
                    cond6 = (deliverytime_cap(routes[i_route[0]] + routes[i_route[1]]) < deliverytimecountcap)
    
                    if cond1 and cond2:
                        if cond3 and cond4 and cond5 and cond6:
                            route_temp = merge(routes[i_route[0]], routes[i_route[1]], node_sel)
                            temp1 = routes[i_route[0]]
                            temp2 = routes[i_route[1]]
                            routes.remove(temp1)
                            routes.remove(temp2)
                            routes.append(route_temp)
                            if link[0] in node_list:
                                node_list.remove(link[0])
                            if link[1] in node_list:
                                node_list.remove(link[0])
                            print('\t','Link ', link, ' fulfills criteria c), so route ', temp1, ' and route ', temp2, ' are merged')
                        else:
                            print('\t','Though Link ', link, ' fulfills criteria c), it exceeds maximum load/distance/time, so skip this link.')
                            continue
                    else:
                        print('\t','For link ', link, ', Two nodes are found in two different routes, but not all the nodes fulfill interior requirement, so skip this link')
                        continue
                else:
                    print('\t','Link ', link, ' is already included in the routes')
                    continue

        for route in routes:
            timeremaining = deliverytimecountcap - deliverytime_cap(route)
            print('\t','route: ', route, ' with load ',sum_cap(route), 'with travelled distane of ', distance_cap(route), 'and time taken is ', time_cap(route),' minutes', 'with delivery time remaining', timeremaining)
    else:
        print('-------')
        print('All nodes are included in the routes, algorithm closed')
        break

    remaining = bool(len(node_list) > 0)

# check if any node is left, assign to a unique route
for node_o in node_list:
    if newnodes.CUBE[node_o] != 0:
        routes.append([node_o])

#adding order id's related to routes
for route in routes:
    for location in route:
        orderid.append(newnodes.NEWORDERID[location])
    orderid.insert(0,0)
    #print('Order IDs found are: ', orderid)
    for order in orderid:
        print(str(order).split(',')[0])
        if str(order).count(',') == 2:
            print(str(order).split(',')[1])
            print(str(order).split(',')[2])
        elif str(order).count(',') == 1:
            print(str(order).split(',')[1])
    orderid = []


# add depot to the routes
for route in routes:
    route.insert(0,20)
    route.append(20)

print('------')
print('Routes found are: ')
print(routes)


[8, 10, 13, 17, 19, 21, 25, 26, 27, 29, 30, 31, 34, 36, 37, 38, 40, 43, 46, 51, 52, 53, 59, 60, 61, 62, 64, 65, 69, 70, 74, 87, 88, 96, 97, 100, 103, 104, 107, 110, 114, 115, 116, 118, 123]
step  1 :  link [121, 117]
step  2 :  link [120, 117]
step  3 :  link [121, 120]
step  4 :  link [117, 113]
step  5 :  link [123, 122]
step  6 :  link [121, 113]
step  7 :  link [120, 113]
step  8 :  link [122, 117]
step  9 :  link [123, 117]
step  10 :  link [123, 121]
step  11 :  link [122, 113]
step  12 :  link [122, 121]
step  13 :  link [122, 120]
step  14 :  link [123, 120]
step  15 :  link [123, 113]
step  16 :  link [117, 116]
step  17 :  link [121, 116]
step  18 :  link [122, 114]
step  19 :  link [120, 114]
step  20 :  link [123, 114]
	 Link  [123, 114]  fulfills criteria a), so it is created as a new route
	 route:  [123, 114]  with load  368 with travelled distane of  375 and time taken is  622.5  minutes with delivery time remaining 256.5
step  21 :  link [120, 116]
	 route:  [123, 114]

	 route:  [110, 118, 123, 114, 116, 115]  with load  1410 with travelled distane of  392 and time taken is  798.0  minutes with delivery time remaining 58.5
step  109 :  link [122, 108]
	 route:  [110, 118, 123, 114, 116, 115]  with load  1410 with travelled distane of  392 and time taken is  798.0  minutes with delivery time remaining 58.5
step  110 :  link [123, 108]
	 route:  [110, 118, 123, 114, 116, 115]  with load  1410 with travelled distane of  392 and time taken is  798.0  minutes with delivery time remaining 58.5
step  111 :  link [114, 108]
	 route:  [110, 118, 123, 114, 116, 115]  with load  1410 with travelled distane of  392 and time taken is  798.0  minutes with delivery time remaining 58.5
step  112 :  link [111, 109]
	 route:  [110, 118, 123, 114, 116, 115]  with load  1410 with travelled distane of  392 and time taken is  798.0  minutes with delivery time remaining 58.5
step  113 :  link [112, 109]
	 route:  [110, 118, 123, 114, 116, 115]  with load  1410 with travell

	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
step  201 :  link [109, 107]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
step  202 :  link [110, 107]
	 Though Link  [110, 107]  fulfills criteria b), it exceeds maximum load/distance/time, so skip this link.
step  203 :  link [109, 104]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
step  204 :  link [110, 104]
	 Link  [110, 104]  is already included in the routes
step  205 :  link [118, 104]
	 Link  [118, 104]  is already included in the routes
step  206 :  link [110, 105]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minut

	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [103, 107, 100]  with load  466 with travelled distane of  302 and time taken is  543.0  minutes with delivery time remaining 256.5
step  271 :  link [109, 101]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [103, 107, 100]  with load  466 with travelled distane of  302 and time taken is  543.0  minutes with delivery time remaining 256.5
step  272 :  link [121, 80]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [103, 107, 100]  with load  466 with travelled distane of  302 and time taken is  543.0  minutes with delivery time remaining 256.5
step  273 :  link [110, 101]
	 

	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [103, 107, 100]  with load  466 with travelled distane of  302 and time taken is  543.0  minutes with delivery time remaining 256.5
	 route:  [97, 96]  with load  953 with travelled distane of  250 and time taken is  465.0  minutes with delivery time remaining 316.5
step  316 :  link [121, 79]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [103, 107, 100]  with load  466 with travelled distane of  302 and time taken is  543.0  minutes with delivery time remaining 256.5
	 route:  [97, 96]  with load  953 with travelled distane of  250 and time taken is  465.0  minutes with delivery time remaining 316.5
step  317 :  link [123, 78]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 wit

...

	 route:  [61, 62, 60, 65, 64, 59, 19]  with load  1528 with travelled distane of  269 and time taken is  643.5  minutes with delivery time remaining 7.5
	 route:  [70, 69]  with load  573 with travelled distane of  206 and time taken is  429.0  minutes with delivery time remaining 319.5
	 route:  [21, 36, 38, 37, 34, 43, 29, 31, 30]  with load  3159 with travelled distane of  51 and time taken is  616.5  minutes with delivery time remaining 0.0
	 route:  [13, 51, 8, 25, 27, 26]  with load  2789 with travelled distane of  78 and time taken is  428.88  minutes with delivery time remaining 183.12
step  6426 :  link [70, 30]
	 Though Link  [70, 30]  fulfills criteria c), it exceeds maximum load/distance/time, so skip this link.
step  6427 :  link [94, 17]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [40, 52, 97, 96, 53]  with load  1575 with travelled distane of  

	 route:  [61, 62, 60, 65, 64, 59, 19]  with load  1528 with travelled distane of  269 and time taken is  643.5  minutes with delivery time remaining 7.5
	 route:  [70, 69]  with load  573 with travelled distane of  206 and time taken is  429.0  minutes with delivery time remaining 319.5
	 route:  [21, 36, 38, 37, 34, 43, 29, 31, 30]  with load  3159 with travelled distane of  51 and time taken is  616.5  minutes with delivery time remaining 0.0
	 route:  [13, 51, 8, 25, 27, 26]  with load  2789 with travelled distane of  78 and time taken is  428.88  minutes with delivery time remaining 183.12
step  6446 :  link [111, 62]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [40, 52, 97, 96, 53]  with load  1575 with travelled distane of  302 and time taken is  633.0  minutes with delivery time remaining 16.5
	 route:  [10, 103, 107, 100, 74, 87, 88]  with load  1043 w

	 route:  [21, 36, 38, 37, 34, 43, 29, 31, 30]  with load  3159 with travelled distane of  51 and time taken is  616.5  minutes with delivery time remaining 0.0
	 route:  [13, 51, 8, 25, 27, 26]  with load  2789 with travelled distane of  78 and time taken is  428.88  minutes with delivery time remaining 183.12
step  6466 :  link [18, 2]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [40, 52, 97, 96, 53]  with load  1575 with travelled distane of  302 and time taken is  633.0  minutes with delivery time remaining 16.5
	 route:  [10, 103, 107, 100, 74, 87, 88]  with load  1043 with travelled distane of  329 and time taken is  703.5  minutes with delivery time remaining -39.0
	 route:  [61, 62, 60, 65, 64, 59, 19]  with load  1528 with travelled distane of  269 and time taken is  643.5  minutes with delivery time remaining 7.5
	 route:  [70, 69]  with load  573 wit

	 route:  [61, 62, 60, 65, 64, 59, 19]  with load  1528 with travelled distane of  269 and time taken is  643.5  minutes with delivery time remaining 7.5
	 route:  [70, 69]  with load  573 with travelled distane of  206 and time taken is  429.0  minutes with delivery time remaining 319.5
	 route:  [21, 36, 38, 37, 34, 43, 29, 31, 30]  with load  3159 with travelled distane of  51 and time taken is  616.5  minutes with delivery time remaining 0.0
	 route:  [13, 51, 8, 25, 27, 26]  with load  2789 with travelled distane of  78 and time taken is  428.88  minutes with delivery time remaining 183.12
step  6485 :  link [66, 40]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [40, 52, 97, 96, 53]  with load  1575 with travelled distane of  302 and time taken is  633.0  minutes with delivery time remaining 16.5
	 route:  [10, 103, 107, 100, 74, 87, 88]  with load  1043 wi

	 For Link  [116, 17] , node  116  is interior to route  [110, 118, 123, 114, 116, 115, 104] , so skip this link
step  6505 :  link [106, 17]
	 route:  [110, 118, 123, 114, 116, 115, 104]  with load  1522 with travelled distane of  397 and time taken is  835.5  minutes with delivery time remaining 21.0
	 route:  [40, 52, 97, 96, 53]  with load  1575 with travelled distane of  302 and time taken is  633.0  minutes with delivery time remaining 16.5
	 route:  [10, 103, 107, 100, 74, 87, 88]  with load  1043 with travelled distane of  329 and time taken is  703.5  minutes with delivery time remaining -39.0
	 route:  [61, 62, 60, 65, 64, 59, 19]  with load  1528 with travelled distane of  269 and time taken is  643.5  minutes with delivery time remaining 7.5
	 route:  [70, 69]  with load  573 with travelled distane of  206 and time taken is  429.0  minutes with delivery time remaining 319.5
	 route:  [21, 36, 38, 37, 34, 43, 29, 31, 30]  with load  3159 with travelled distane of  51 and tim